In [6]:
import pickle
import numpy
import chessboard
import park_martin
import yaml
numpy.set_printoptions(linewidth=300, suppress=True)
from scipy.linalg import expm, inv
from numpy import dot, eye
import sys
import torch
import numpy as np

In [7]:
eef_poses = [
    [3.008, -0.668, 0.549, -0.16574, -0.268, 0.5065], # right back 0
    [3.008, -0.5914, 0.633, -0.111, -0.2634, 0.485], # right back 1
    [-2.31092, -0.24056, -0.99504, -0.21117, -0.12188, 0.41125], #right back 2
    [-2.51890, -0.54126, -0.08807, -0.00074, -0.49342, 0.42817], # right back corner
    [-3.008, -0.668, -0.549, -0.16574, 0.268, 0.5065], # left back 0
    [-3.008, -0.5914, -0.633, -0.111, 0.2634, 0.485], # left back 1
    [-3.008, -0.5914, -0.633, -0.061, 0.2634, 0.485], # left back 1 x + 5cm
    [-3.008, -0.5914, -0.633, -0.011, 0.2634, 0.485], # left back 1 x + 10cm
    [2.31092, -0.24056, 0.99504, -0.21117, 0.12188, 0.41125], # left back 2
    [2.39645, -0.54843, 0.08445, -0.00101, 0.49278, 0.42958], # left back corner
]

In [8]:
def euler_to_rotation_matrix(roll, pitch, yaw):
    """
    Convert euler angles (roll, pitch, yaw) to a rotation matrix.
    """
    R_x = torch.tensor([[1, 0, 0],
                        [0, torch.cos(roll), -torch.sin(roll)],
                        [0, torch.sin(roll), torch.cos(roll)]])
    
    R_y = torch.tensor([[torch.cos(pitch), 0, torch.sin(pitch)],
                        [0, 1, 0],
                        [-torch.sin(pitch), 0, torch.cos(pitch)]])
    
    R_z = torch.tensor([[torch.cos(yaw), -torch.sin(yaw), 0],
                        [torch.sin(yaw), torch.cos(yaw), 0],
                        [0, 0, 1]])
    
    R = torch.matmul(R_z, torch.matmul(R_y, R_x))
    return R
    
def pose_to_transform(batch):
    """
    Construct a batch of transformation matrices from a batch of roll, pitch, yaw, x, y, z.
    The input batch should have the shape (n, 6), where each row is (roll, pitch, yaw, x, y, z).
    The output will have the shape (n, 4, 4), representing the transformation matrices.
    """
    n = batch.size(0)
    transformation_matrices = torch.zeros((n, 4, 4))
    
    for i in range(n):
        roll, pitch, yaw, x, y, z = batch[i]
        rotation_matrix = euler_to_rotation_matrix(roll, pitch, yaw)
        transformation_matrix = torch.eye(4)
        transformation_matrix[:3, :3] = rotation_matrix
        transformation_matrix[:3, 3] = torch.tensor([x, y, z])
        transformation_matrices[i] = transformation_matrix
    
    return transformation_matrices

In [58]:
eff_poses_tor_o=pose_to_transform(torch.tensor(eef_poses))

In [59]:
im_poses_o=torch.load("im_poses_not_inv.tar").cpu().detach()
im_poses_o[:,:3,3]=im_poses_o[:,:3,3]*2.795

In [60]:
eff_poses_tor=eff_poses_tor_o[[0,1,2,3,4,7,8,9]]
im_poses=im_poses_o[[0,1,2,3,4,7,8,9]]

In [61]:
im_poses

tensor([[[ 0.5608,  0.5987, -0.5719,  0.3918],
         [-0.6128,  0.7646,  0.1995, -0.1302],
         [ 0.5568,  0.2386,  0.7957,  0.1671],
         [ 0.0000,  0.0000,  0.0000,  1.0000]],

        [[ 0.4756,  0.6831, -0.5543,  0.3721],
         [-0.6430,  0.6999,  0.3109, -0.1338],
         [ 0.6003,  0.2086,  0.7721,  0.2045],
         [ 0.0000,  0.0000,  0.0000,  1.0000]],

        [[ 0.7464, -0.5667, -0.3488,  0.3081],
         [ 0.6257,  0.7761,  0.0780, -0.0323],
         [ 0.2265, -0.2765,  0.9340,  0.1216],
         [ 0.0000,  0.0000,  0.0000,  1.0000]],

        [[ 0.6885,  0.1953, -0.6985,  0.4895],
         [-0.0081,  0.9651,  0.2618, -0.2207],
         [ 0.7252, -0.1746,  0.6660,  0.3403],
         [ 0.0000,  0.0000,  0.0000,  1.0000]],

        [[ 0.9999,  0.0146, -0.0041,  0.0000],
         [-0.0146,  0.9999, -0.0079,  0.0000],
         [ 0.0040,  0.0080,  1.0000,  0.0000],
         [ 0.0000,  0.0000,  0.0000,  1.0000]],

        [[ 0.9964, -0.0588,  0.0616, -0.0486],
   

In [62]:
A, B = [], []
for i in range(1,len(im_poses)):
    p = eff_poses_tor[i-1], im_poses[i-1]
    n = eff_poses_tor[i], im_poses[i]
    A.append(dot(inv(p[0]), n[0]))
    B.append(dot(inv(p[1]), n[1]))

In [63]:
X = eye(4)
Rx, tx = park_martin.calibrate(A, B)
X[0:3, 0:3] = Rx
X[0:3, -1] = tx

In [64]:
Rx

array([[-0.00080457, -0.95986807,  0.28045077],
       [ 0.99996944, -0.00295324, -0.00723896],
       [ 0.00777668,  0.28043638,  0.95984111]])

In [73]:
tmp_list=[]
for i in range(len(im_poses)):
    rob = eff_poses_tor[i]
    obj = im_poses[i]
    tmp = dot(rob, dot(X, inv(obj)))
    tmp_list.append(tmp)
tmp_tor=torch.tensor(tmp_list)

In [75]:
# rob = eff_poses_tor[0]
# obj = im_poses[0]
# world_pose = dot(dot(rob, X), inv(obj))
# print(world_pose)
world_pose=tmp_tor.mean(dim=0)

In [76]:
c_pos=torch.tensor(world_pose).float()@im_poses_o

<ipython-input-76-4811cd8f0c78>:1: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [85]:
im_poses_o.shape

torch.Size([10, 4, 4])

In [77]:
c_pos_n=c_pos[:,:3,3]

In [78]:
eff_poses_n=eff_poses_tor_o[:,:3,3]

In [79]:
import plotly.graph_objects as go
fig = go.Figure()

fig.add_trace(go.Scatter3d(x=c_pos_n[:, 0].detach().cpu(),  # X coordinates
    y=c_pos_n[:, 1].detach().cpu(),  # Y coordinates
    z=c_pos_n[:, 2].detach().cpu(),  # Z coordinates
                           mode='markers', marker=dict(size=5, color='red'),name="cams"))
fig.add_trace(go.Scatter3d(x=eff_poses_n[:, 0].detach().cpu(),  # X coordinates
    y=eff_poses_n[:, 1].detach().cpu(),  # Y coordinates
    z=eff_poses_n[:, 2].detach().cpu(),  # Z coordinates
                           mode='markers', marker=dict(size=5, color='blue'),name="eef"))

fig.update_layout(scene=dict(
                    xaxis=dict(range=[-0.6, 0.6]),
                    yaxis=dict(range=[-0.6, 0.6]),
                    zaxis=dict(range=[0, 1.2])
))

fig.update_layout(scene=dict(xaxis_title='X', yaxis_title='Y', zaxis_title='Z'),
                  title="Camera Positions and Orientations")

fig.update_layout(width=1000, height=700)
fig.show()

In [99]:
pc_tor=torch.load("pts_tor.tar").cpu().detach()[::30]*2.795

In [100]:
pc_tor.shape

torch.Size([52560, 3])

In [101]:
#pc_pos=(torch.tensor(world_pose).float()[:3,:3]@pc_tor.T).T

In [102]:
def transform_points(points, matrix):
    """
    Applies a transformation to a set of 3D points.

    Parameters:
    - points: A torch tensor of size (n, 3) representing n 3D points.
    - matrix: A torch tensor of size (4, 4) representing the transformation matrix.

    Returns:
    - A torch tensor of size (n, 3) of transformed 3D points.
    """
    # Check if the inputs are torch tensors
    if not isinstance(points, torch.Tensor) or not isinstance(matrix, torch.Tensor):
        raise ValueError("Both points and matrix must be torch.Tensor objects.")
    
    # Check the shape of the points and the matrix
    if points.shape[1] != 3 or matrix.shape != (4, 4):
        raise ValueError("Invalid shape for points or matrix. Points should be (n, 3) and matrix should be (4, 4).")
    
    # Add an extra dimension of ones to the points tensor to make it compatible with the transformation matrix
    ones = torch.ones(points.shape[0], 1, dtype=points.dtype, device=points.device)
    points_homogeneous = torch.cat([points, ones], dim=1)  # Convert points to homogeneous coordinates
    
    # Apply the transformation matrix to the points
    transformed_points_homogeneous = torch.mm(points_homogeneous, matrix.t())  # Multiply by the transpose of the matrix
    
    # Convert back from homogeneous coordinates by dropping the last dimension
    transformed_points = transformed_points_homogeneous[:, :3]
    
    return transformed_points

In [103]:
pc_pos=transform_points(pc_tor,torch.tensor(world_pose).float())

<ipython-input-103-66a67db53092>:1: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [105]:
fig = go.Figure()

fig.add_trace(go.Scatter3d(x=c_pos_n[:, 0].detach().cpu(),  # X coordinates
    y=c_pos_n[:, 1].detach().cpu(),  # Y coordinates
    z=c_pos_n[:, 2].detach().cpu(),  # Z coordinates
                           mode='markers', marker=dict(size=5, color='red'),name="cams"))
fig.add_trace(go.Scatter3d(x=eff_poses_n[:, 0].detach().cpu(),  # X coordinates
    y=eff_poses_n[:, 1].detach().cpu(),  # Y coordinates
    z=eff_poses_n[:, 2].detach().cpu(),  # Z coordinates
                           mode='markers', marker=dict(size=5, color='blue'),name="eef"))

fig.add_trace(go.Scatter3d(x=pc_pos[:, 0].detach().cpu(),  # X coordinates
    y=pc_pos[:, 1].detach().cpu(),  # Y coordinates
    z=pc_pos[:, 2].detach().cpu(),  # Z coordinates
                           mode='markers', marker=dict(size=0.3, color='green'),name="point_cloud"))

# fig.update_layout(scene=dict(
#                     xaxis=dict(range=[-0.6, 0.6]),
#                     yaxis=dict(range=[-0.6, 0.6]),
#                     zaxis=dict(range=[0, 1.2])
# ))

fig.update_layout(scene=dict(xaxis_title='X', yaxis_title='Y', zaxis_title='Z'),
                  title="Camera Positions and Orientations")

fig.update_layout(width=1000, height=700)
fig.show()